Lecture notes for the course
# Computer-Guided Data Analysis
in the Bachelor's study program in Physics at Karlsruhe Institute of Technology (KIT)

U. Husemann (based on material from G. Quast, T. Ferber and U. Husemann)

Summer Semester 2024

# Chapter 4: Statistical Data Analysis II - Parameter Estimation (Part 1)
**Parameter estimation** is a branch of mathematical statistics and an important tool in physics. The task and aim of parameter estimation is to estimate a (hopefully small) number of model parameters from a potentially very large amount of data. We understand the term "estimation" in the sense of a systematic procedure for determining a (in a certain sense optimal) value and an uncertainty for the model parameters. Statistically speaking, we infer the properties of a probability distribution from a sample, for example its expected value and standard deviation. We use the arithmetic mean and sample standard deviation of the sample as estimated values.

>**Example: Lifetime of cosmic muons** In an experiment, the lifetime of muons from cosmic rays is to be determined. Muons are sibling particles of electrons, but have a mass 200 times greater and are not stable, but decay in around 2.2 microseconds. Their lifetime can be determined by stopping them in matter and then determining the time between capture and decay. The physics model for this process is an exponential decay with the PDF $f(t;\tau)=1/\tau\exp[-t/\tau]$, where the scaling parameter $\tau$ corresponds to the mean lifetime of the muon. In the following code example (which was already used in a similar way in Chapter 2 to illustrate uncertainty bars), this is simulated and then the mean lifetime and its uncertainty are estimated.

In [ ]:
"""model muon lifetime and its estimate"""
import numpy as np
import matplotlib.pyplot as plt

rng = np.random.default_rng()
n = 100
tau_true = 2.2e-6
data = rng.exponential( scale=tau_true, size=n )

fig,ax = plt.subplots()

# lines at the random data
ax.vlines( data, 0, 1, linestyles='-', lw=2)

# box-whisker plot to illustrate distribution
boxy = 2.
ax.boxplot( data, positions=[boxy], vert=False , notch=False )

# estimate tau and its uncertainty
meanx = np.mean( data )
meany = 3.
stdx  = np.std( data, ddof=1 )/np.sqrt( len(data) )
ax.errorbar( meanx, meany, xerr=stdx, fmt='-ro' )
ax.text( 1.2*meanx, meany-0.05, r"$\hat\tau = %4.2f \pm %4.2f\, \mathsf{\mu s}$" % ( 1e6*meanx, 1e6*stdx ) )


ax.set_ylim( 0, 4 )
ax.set_yticks ( [] )
ax.ticklabel_format( style='sci', scilimits=(-6,-6), axis='x' )
ax.set_xlabel( "$t (s)$") 

plt.show()

Another typical task of parameter estimation is **fitting a model function** to data in order to estimate the function's free parameters and their uncertainty. If the model is a physics model, e.g. represents a partial aspect of a physical law, the corresponding physical parameters can be estimated directly by the fit. The simplest example of this is the "straight-line fit", where the model is a linear function $y=mx+c$ with the parameters slope $m$ and $y$-intercept $c$. The technical term for this class of fitting tasks is "**linear regression**". Here, "linear" refers to linearity in the parameters (here: $m$ and $c$), while the independent variables (here: $x$) do not necessarily have to be linear in the model function.

>**Example: Determining electral resistance**: A current-voltage characteristic of an electrical resistor with unknown resistance $R$ is recorded. For this purpose, fixed electrical voltages $V$ that are assumed to be exactly known are applied to the resistor and the current $I(V)$ is measured. The only uncertainty of the individual current measurements is the reading accuracy of the scale of the measuring device, which is taken into account as a statistical uncertainty. Both assumptions are simplifications that are frequently used in  physics laboratory courses, but are not always justified. The model function $I(V) = 1/R\cdot U$ is fitted to the data points using linear regression. The parameter of this physics model is the slope $1/R$, also known as the electrical conductance $G$. From the estimated value and uncertainty of $G$, $\hat G\pm \sigma_{\hat G}$, the uncertainty on $R=1/G$ is then determined using uncertainty propagation ($G$ and $1/G$ have the same relative uncertainty) in order to arrive at the result $\hat R \pm \sigma_{\hat R}$. Fitting directly with $R$ as a model parameter is also easily possible with today's software, but this model function is then no longer linear in the model parameter, and therefore the fit is not a linear regression. The following code example simulates the current-voltage characteristic with random numbers and uses (in anticipation of further sections in this chapter) a SciPy routine for linear regression. The conductance is compatible with the true value 0.001 siemens within its uncertainties.

In [ ]:
"""Using SciPy.optimize.curve_fit for a straight-line fit to Ohm's law"""
import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit

def current_ohm_model( V, G=1. ):
	'''Ohm's law'''
	return G*V

# generate N data points
N = 11

# minimum/maximum voltage in volts
Vmin, Vmax = 1, 10

# resistance in ohm, conductance in siemens
R = 1000
G = 1/R

# current uncertainty in A (from limited resolution of ammeter)
sigmaI = np.ones(N)*5e-4

rng = np.random.default_rng( 42 )

# generate data points according to Ohm's law shifted by random offset
V = np.linspace( Vmin, Vmax, N )
I = current_ohm_model( V, G ) + rng.normal( size=N, scale=sigmaI )

# plot data points
fig,ax = plt.subplots()
plt.errorbar( V, I, sigmaI,fmt='bo') 
plt.xlabel('$V$ (V)')
plt.ylabel('$I$ (A)')

# fit with curve_fit (uncertainty only correct when explicitly switching on absolute uncertainites)
popt, pcov = curve_fit( current_ohm_model, V, I, sigma=sigmaI, absolute_sigma=True )

# plot fitted curve
Vrange = np.linspace( Vmin-0.5, Vmax+0.5, 200 )
ax.plot( Vrange, current_ohm_model( Vrange, *popt), 'r-' )

# print fit parameters
ax.text( Vmin, 0.010, r"$G$ = %5.3f $\pm$ %5.3f mS" % ( 1e3*popt[0], 1e3*np.sqrt(pcov[0][0]) ) )

plt.show()

Generally speaking, parameter estimation answers the question of which choice of model parameters leads to the best fit of a given **model function to the data**. There are several approaches for parameter estimation in the literature:
- In this course, we will discuss the **least squares method** (LS, also called $\chi^2$ method), which was developed in the early 19th century by Carl Friedrich Gauss, Pierre-Simon Laplace and Adrien-Marie Legendre. The linear regression for adjustments, e.g., for the straight-line fit in the physics laboratory course (see code example above), is an example of this method. A further description of the LS method and its practical application can be found in the short writeput [Function fitting with the $\chi^2$ method](https://etpwww.etp.kit.edu/~quast/Skripte/Chi2Method.pdf) (in German) by Günter Quast.
- Later in your studies, you will become familiar with a more modern method, the **Maximum Likelihood Method** (ML) developed by Ronald Aylmer Fischer. It is universally applicable for systematically constructing estimators with "optimal" properties. These include an unbiased ("true to expectation") estimate of the true value and the smallest possible variance. A first introduction to ML methods can be found at the end of this chapter in the outlook section.

## Least squares method
The method of least squares is based on minimizing the distance between a model and data at $n$ positions $x_i$. The model parameters are optimized so that the total distance is as small as possible. The residual, i.e., the squared distance normalized to the variance, is used as the distance measure for a data point $y_i$ with a variance $\sigma_i^2$ at a position $x_i$ from the model expectation $\lambda_i$.
$$
d_i^2\equiv\frac{(y_i-\lambda_i)^2}{\sigma_i^2}.
$$
The residual sum of squares (RSS) $S$, often called $\chi^2$ in the literature, is then used as the total distance:
$$
S \equiv \chi^2 \equiv \sum_{i=1}^n d_i^2 \equiv \sum_{i=1}^n\frac{(y_i-\lambda_i)^2}{\sigma_i^2}.
$$

For a straight-line fit, these quantities can be found in the following sketch

<img src="img/straight_line_fit.png" width=50%>

>**Note: $S$ or $\chi^2$?** The relationship between the residual sum of squares and the $\chi^2$ distribution has already been explained in Chapter 2: for normally distributed measured values $y_i$, $S$ follows a $\chi^2$ distribution with a certain number of degrees of freedom. In the literature, the function $S$ itself is therefore often simply referred to as $\chi^2$, and the least squares method is also called the **$\chi^2$ method**. To better distinguish between the residual sum of squares $S$ and the $\chi^2$ distribution, the symbol $S$ is used here and in the following for the residual sum of squares.

The variables used in the LS method are defined as follows:
- $x_i$ ($i=1,\dots,n$) is the $i$-th position and is assumed to be **exactly known**. This is not always a good assumption for measurement data, as they usually also contain uncertainties in $x_i$. However, this case is not easy to handle with a standard LS fit (and with standard tools). This situation will be addressed again in the section on function fitting in practice below.
- $y_i$ is the measured value or data point at position $x_i$.
- $\lambda_i$ is the true value of the model function at position $x_i$. The model function contains $m$ parameters $\mathbf{a}=(a_1,\dots,a_m)$, i.e., $\lambda_i = \lambda_i(x_i;\mathbf{a})$, so the true value of $\lambda_i$ is **unknown**. The fit determines the parameter values $\hat{\mathbf{a}}$ that optimally fit the data. The linear LS method requires the model function to be linear in $\mathbf{a}$ (but not necessarily linear in $x_i$).
- $\sigma_i^2$ is the variance of the true value $\lambda_i$ at position $x_i$. It is assumed to be **known**. In many branches of science, $\sigma_i^2=1$ is set for a linear regression.
This indicates that there is no useful model of the associated uncertainties. In physics, on the other hand, such uncertainty models are known or the uncertainties can be estimated from the data using the sample variance.


>With the **least squares method**, the estimated values $\hat{\mathbf{a}}$ for the parameters of a model function $\lambda_i(x_i;\mathbf{a})$ is obtained by minimizing the residual sum of squares:
>$$
S \equiv \chi^2\equiv \sum_{i=1}^{n} \frac{(y_i - \lambda_i(x_i;\mathbf{a}))^2}{\sigma_i^2}
\overset{!}{=}\mathsf{min}
>$$

Here are two further **comments** on the method of least squares:
- $S=S(\mathbf{a})$ is a **scalar** function of the **parameters**. It is calculated by inserting the data points $y_i$ and variances $\sigma_i^2$, therefore these are **not** independent variables. The minimization of $S$ is therefore a **minimization in parameter space**, not in the space of measured values.
- The LS method used in physics is known as the **weighted least squares (WLS) method**. The LS method without uncertainties is referred to in the statistical literature as the **ordinary least squares (OLS) method**. The following variable is minimized in the OLS method:
$$
S_\mathsf{OLS} \equiv \sum_{i=1}^n(y_i-\lambda_i)^2 \overset{!}{=}\mathsf{min}
$$
- For correlated measured values $\mathbf{y}=(y_1,\dots,y_n)$ and known covariance matrix $\mathbf{V}$ of the model function $\boldsymbol{\lambda}=(\lambda_1,\dots,\lambda_n)$, the method of least squares can be generalized by replacing the residual sum of squares by the Mahalanobis distance. This is referred to in the statistical literature as the **generalized least squares (GLS) method**. In the GLS method, the following expression is minimized:
$$
S \equiv \chi^2 \equiv
(\mathbf{y} - \boldsymbol{\lambda}(\mathbf{x};\mathbf{a}))^\mathsf{T} \,
\mathbf{V}^{-1} \,
(\mathbf{y} - \boldsymbol{\lambda}(\mathbf{x};\mathbf{a}))
\overset{!}{=}\mathsf{min}
$$

### Minimization of the residual sum of squares
The minimization of $S(\mathbf{a})$ can be done **analytically** in some simple cases. The necessary condition for a minimum is that the partial derivatives with respect to all $a_i$ vanish:
$$
\frac{\partial S}{\partial a_i} \overset{!}{=} 0 \quad \textsf{for } i = 1, \dots, m
$$
This can also be summarized as a gradient with respect to $\mathbf{a}$:
$$
\boldsymbol{\nabla}_\mathbf{a} S \equiv \textsf{grad}_\mathbf{a} S\overset{!}{=} 0
$$
In general, the minimization is performed **numerically**. For this purpose, there are efficient algorithms for **numerical optimization** of scalar functions in an $m$-dimensional parameter space. The boom in machine learning in the last decade has led to the development of new, extremely powerful algorithms in this field. In practice, and if the minimization is not time-critical, even simple cases are treated numerically.

### Analytical least squares
#### Constant model function
As an example of the analytical minimization of $S$, the simple case of a constant model function $\lambda_i = a$ is considered first. This model function is obviously linear in $a$, and linear regression is applicable. The LS method requires the minimization of
$$
S = \sum_{i=1}^{n}\frac{(y_i-a)^2}{\sigma^2}.
$$
The task of comparing $n$ measured values $y_i$ with a constant and thus finding the best "fitting" constant overall corresponds to the search for an average value for the $y_i$. The result of the calculation should therefore be an LS estimate of the mean value of data. We distinguish between two cases:

**Equal variance** for each measured value: $\sigma_i^2\equiv\sigma^2$. In this case, the optimal parameter $a$ is determined via
$$
\frac{\partial S}{\partial a} =
\sum_{i=1}^{n} \frac{-2(y_i-a)}{\sigma^2} =
-\frac{2}{\sigma^2}\left( \sum_{i=1}^{n} y_i - n\cdot a \right)\overset{!}{=}0,
$$
where constants were drawn in front of the sums. This expression is zero if the expression in brackets is zero, i.e.,
$$
\hat a = \frac{1}{n} \sum_{i=1}^{n} y_i.
$$
This is the well known **arithmetic mean** of the $y_i$. The LS method has therefore "automatically" provided us with the arithmetic mean of the measurement data as the LS estimate of the true value by which the measurement data scatter.

This minimization of $S$ as a function of the parameter $a$ could also have been carried out **numerically**. We can illustrate this here in a code example by inserting a series of possible values of $a$ into the above equation and determining $S$ for each value ("parameter scan"). Then $S$ is plotted as a function of $a$, resulting in a parabola in parameter space. A numerical algorithm would then search for the minimum of $S(a)$. We will come back to the relationship between the width of the parabola and the uncertainty of the estimate of $a$ later in this chapter.

In [ ]:
"""animated_leastSquares: illustration of least squares method"""
# U. Husemann, June 2021

# add this Jupyter magic command to enable animation on some systems (needs ipympl installed)
%matplotlib ipympl

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as anim

# model
atrue = 3
sig   = 1

# data points
n = 10
xi = np.linspace( 1, n, n )

# scan possible values of parameter a
amin, amax, steps = 0., 6., 300
a = np.linspace( amin, amax, steps )

rng = np.random.default_rng( 42 )
yi = rng.normal( loc=atrue, scale=sig, size=n )

fig,ax = plt.subplots( 2, 1, figsize=(7,10) )
graph_data  = ax[0].errorbar( xi, yi, yerr=sig, fmt='ro')
graph_line, = ax[0].plot( [], [], 'b-', lw=2 )
graph_S,    = ax[1].plot( [], [], 'b-', lw=2 )
ax[0].set_xlabel( r"$x$")
ax[0].set_ylabel( r"$y$")
ax[0].set_ylim( amin, amax )
ax[1].set_xlabel( r"$a$")
ax[1].set_ylabel( r"$S$")
ax[1].set_xlim( amin, amax )
ax[1].set_ylim( 0, 100 )

def S( a, y, sig=1. ):
	return np.sum( ( ( y - a ) / sig )**2 )

def animate( step ):
	a_anim = a[:step+1]
	S_anim = [ S( a, yi, sig ) for a in a_anim ]
	graph_line.set_data( [0.5,10.5], [a_anim[-1],a_anim[-1]] )
	graph_S.set_data( a_anim, S_anim )
	return graph_line, graph_S

ani = anim.FuncAnimation( fig, animate, frames=steps, interval=30, repeat=False )
plt.show()

**Different variances** for each measured value: in this case, the necessary condition for a minimum is
$$
\frac{\partial S}{\partial a} =
\sum_{i=1}^{n} \frac{-2(y_i-a)}{\sigma_i^2} =
-2\left( \sum_{i=1}^{n} \frac{y_i}{\sigma_i^2} - a \sum_{i=1}^{n} \frac{1}{\sigma_i^2}\right)\overset{!}{=}0
$$
This expression is also zero if the expression in brackets is zero. With the weight factor $w_i = 1/\sigma_i^2$, this condition can be rewritten as follows
$$
\sum_{i=1}^{n} w_i\cdot y_i \overset{!}{=} a \sum_{i=1}^{n} w_i
$$
and thus we obtain the LS estimate for $a$:
$$
\hat a = \frac{1}{\sum_i w_i} \sum_{i=1}^{n} w_i\cdot y_i.
$$
This is also an average of the measured data, with the difference that each measured value $y_i$ is multiplied by the weight factor $w_i$, which determines its "importance" for the average value. The variable is referred to as the **weighted mean** $\overline{x}$. The weighting factor is the reciprocal of the variance, $w_i = 1/\sigma_i^2$, so the measured values with the smallest variance are given the greatest weight in the average. The weighted mean value is normalized with the sum of the weights, which takes the place of the number of measured values $n$ in the arithmetic mean. The LS method has therefore "automatically" provided us with a procedure with which measured values with different uncertainties can be averaged in the best possible way.

#### Linear regression
The general case of a linear model function can also be solved analytically, but this requires some linear algebra. There are analytical equations for linear regression that do not require numerical minimization and are implemented in many software packages. The model function $\boldsymbol{\lambda}=(\lambda_1,\dots\lambda_n)^\mathsf{T}$ is given by the vector
$$
\boldsymbol{\lambda} = \mathbf{A}\mathbf{a}
$$
with the parameter vector $\mathbf{a}=(a_1,\dots,a_m)^\mathsf{T}$, a matrix $\mathbf{A}$ with $m$ rows and $n$ columns independent of $\mathbf{a}$, which contains the coefficients of the $a_i$, e.g., functions of the positions $x_i$ (the example of a straight line follows below), and the covariance matrix $\mathbf{V}$. Thus, $S$ is to be minimized as a scalar function of the parameters $\mathbf{a}$
$$
S \equiv \chi^2 \overset{\textsf{lin. Regr.}}{=}
(\mathbf{y} - \mathbf{Aa})^\mathsf{T} \,
\mathbf{V}^{-1} \,
(\mathbf{y} - \mathbf{Aa}).
$$

The results of this minimization are given here first, the calculation follows for all those interested. The estimated value $\hat{\mathbf{a}}$ is determined by minimizing the gradient of $S$ with respect to the parameters, it is the following linear function of the measured values $\mathbf{y}$.
$$
\hat{\mathbf{a}} =
(\mathbf{A}^\mathsf{T}\,\mathbf{V}^{-1}\,\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\,\mathbf{V}^{-1} \mathbf{y} \equiv
\mathbf{B}\mathbf{y}.
$$
The covariance matrix of the parameters $\hat{\mathbf{a}}$ is obtained from this expression by uncertainty propagation (exact for linear functions of the parameters):
$$
\mathbf{V}[\hat{\mathbf{a}}]= \mathbf{B}\mathbf{V}\mathbf{B}^\mathsf{T} = (\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^{-1}.
$$
(Similarities with football club names are purely coincidental and unintentional.)


>**Auxiliary calculation 1: Estimated value for parameter vector $\mathbf{a}$**
>
>Before the gradient is formed with respect to $\mathbf{a}$, we first multiply all terms in $S$:
>$$
S =
\mathbf{y}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} -
\mathbf{y}^\mathsf{T} \mathbf{V}^{-1}  \mathbf{Aa} -
(\mathbf{Aa})^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} +
(\mathbf{Aa})^\mathsf{T} \mathbf{V}^{-1} \mathbf{Aa}.
>$$
> Note that each of these summands is a scalar. We use a matrix notation for this auxiliary calculation, as the known calculation rules for matrices and their inverse and transposed matrix are the quickest and clearest way to obtain the result.
> We now use the calculation rule for the transpose of a product of matrices: $(\mathbf{AB\dots Z})^\mathsf{T} = \mathbf{Z}^\mathsf{T}\dots \mathbf{B}^\mathsf{T} \mathbf{A}^\mathsf{T}$. This gives us $(\mathbf{Aa})^\mathsf{T}=\mathbf{a}^\mathsf{T}\mathbf{A}^\mathsf{T}$ in the third and fourth summands. We also move $\mathbf{a}$ forward in the second summand, noting that the inverse of the covariance matrix, like the covariance matrix itself, is a symmetric matrix and therefore $(\mathbf{V}^{-1})^\mathsf{T}=\mathbf{V}^{-1}$:
>$$
(\mathbf{y}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})\mathbf{a} =
\mathbf{a}^\mathsf{T} (\mathbf{y}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^\mathsf{T} =
\mathbf{a}^\mathsf{T} \mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y}.
>$$
>Thus we get:
>$$
S =
\mathbf{y}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} -
2\mathbf{a}^\mathsf{T} \mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} +
\mathbf{a}^\mathsf{T} (\mathbf{A}^\mathsf{T} \mathbf{V}^{-1})\, \mathbf{Aa}.
>$$
>Now we form the gradient of $S$ with respect to $\mathbf{a}$. The first summand is not dependent on $\mathbf{a}$ and is omitted, and in the last summand, in which $\mathbf{a}$ and $\mathbf{a}^\mathsf{T}$ occur, the product rule is applied:
>$$
\boldsymbol\nabla_\mathbf{a} S=
-2 \mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y}
+2 \mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{Aa}.
>$$
>The gradient of the scalar $S$ is a vector. The LS method states that the necessary condition for estimating $\mathbf{a}$ is the disappearance of this gradient, i.e. $\boldsymbol\nabla_\mathbf{a} S \overset{!}{=}0$ for $\mathbf{a}=\hat{\mathbf{a}}$. We therefore solve for $\hat{\mathbf{a}}$:
>$$
(\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})\,\hat{\mathbf{a}} =
\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y}.
>$$
>By multiplying both sides of this equation by $(\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^{-1}$ from the left we get the solution
>$$
\hat{\mathbf{a}} =
(\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^{-1}
\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} \equiv \mathbf{B} \mathbf{y},
>$$
>where we have abbreviated the product of the five matrices to $\mathbf{B}$. The term in brackets is an $m\times m$-matrix, multiplied by the $m\times n$-matrix $\mathbf{A}^\mathsf{T}$ and the $n\times n$-matrix $\mathbf{V}^{-1}$. This means that $\mathbf{B}$ is an $m\times n$ matrix.

>**Auxiliary calculation 2: Estimated value for covariance matrix of the parameter vector**
>
>To estimate the covariance matrix $\mathbf{V}[\hat{\mathbf{a}}]$ of the parameter vector - not to be confused with the (inverse) covariance matrix of the measured values $\mathbf{V}$ used in the above calculation - we use the linear (Gaussian) law of uncertainty propagation, which is exact for this linear function of the parameters. So far, we have only used variances of scalar functions $u$ of the measured values:
>$$
\mathbf{V}[u] = \sum_{kl} \frac{\partial u}{\partial x_k} \frac{\partial u}{\partial x_l} V_{kl}
>$$
>with the measured values $x_i$ and the elements of the covariance matrix of the measured values $V_{ij}$. We use the component notation in this auxiliary calculation to make the calculation simpler and more transparent. The generalization to vectors $\mathbf{u}$ which are functions of the measured values (such as $\hat{\mathbf{a}}$), and the elements of the covariance matrix $V_{ij}[\mathbf{u}]$ works as follows:
>$$
V_{ij}[\mathbf{u}] =
\mathsf{Cov}(u_i,u_j) =
\sum_{kl} \frac{\partial u_i}{\partial x_k} \frac{\partial u_l}{\partial x_l} V_{kl}.
>$$
>Applied to linear regression, $\mathbf{u}$ corresponds to the parameter vector $\hat{\mathbf{a}}$ and the data $\mathsf{x}$ corresponds to the measurement data $\mathsf{y}$. $\hat{\mathbf{a}}$ is a linear function of the data: $\hat{\mathbf{a}} = \mathbf{By}$ with the above definition of $\mathbf{B}$. This can be calculated:
>$$
V_{ij}[\hat{\mathbf{a}}] =
\sum_{kl} \frac{\partial \hat{a}_i}{\partial y_k} \frac{\partial \hat{a}_j}{\partial y_l} V_{kl},
>$$
>where the partial derivatives are:
>$$
\frac{\partial \hat{a}_i}{\partial y_k} = B_{ik}, \quad
\frac{\partial \hat{a}_j}{\partial y_j} = B_{jl}.
>$$
> This results in
>$$
V_{ij}[\hat{\mathbf{a}}] = \sum_{kl} B_{ik} B_{jl} V_{kl} = \sum_{kl} B_{ik} V_{kl} B_{lj},
>$$
>whereby we transposed and swapped the last two components in the last step, taking into account that $\mathbf{V}$ is symmetrical. In matrix notation, this corresponds to the result given above:
>$$
\mathbf{V}[\hat{\mathbf{a}}]= \mathbf{B}\mathbf{V}\mathbf{B}^\mathsf{T}.
>$$
>
>If $\mathbf{B}$ is already known, the calculation ends here. Otherwise the definition of $\mathbf{B}$,
>$$
\mathbf{B}\equiv
(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}.
>$$
>can still be used to further simplify the expression. We use the calculation rule for the transpose of a product of matrices $(\mathbf{AB\dots Z})^\mathsf{T} = \mathbf{Z}^\mathsf{T}\dots \mathbf{B}^\mathsf{T} \mathbf{A}^\mathsf{T}$ to write:
>$$
\begin{split}
V_{ij}[\hat{\mathbf{a}}]
&= \left[(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\right]
\mathbf{V}
\left[(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\right]^\mathsf{T}\\
&= \left[(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\right]
\mathbf{V}
\left[(\mathbf{V}^{-1})^\mathsf{T} \mathbf{A}
( (\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1} )^\mathsf{T}\right]\\
\end{split}
>$$
>This product of matrices can now be significantly simplified by exploiting the fact that the product of a $d\times d$ square matrix with its inverse is $\mathbf{MM}^{-1} = \mathbf{M^{-1}M} = \mathbf{1}_d$, the unit matrix in $d$ dimensions. We apply this to the covariance matrix and its inverse in the center of the above product. We also note that the $n\times n$-matrices $V$ or $V^{-1}$ and thus also the $m\times m$-matrix $\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A}$ and their inverse are symmetric, so that $M=M^\mathsf{T}$ applies to these matrices. The matrix $\mathbf{A}$ itself is not square and therefore has no inverse. Now some matrices and their inverses cancel:
>$$
\begin{split}
\mathbf{V}[\hat{\mathbf{a}}]
&= \left[(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\right]
\mathbf{V}
\left[\mathbf{V}^{-1} \mathbf{A}
(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}\right]\\
&= (\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}
\underbrace{\mathbf{V}\mathbf{V}^{-1}}_{\mathbf{1}_n}
\mathbf{A}
(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}\\
&= (\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\underbrace{(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})
(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}}_{\mathbf{1}_m}\\
&= (\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1}
\end{split}.
>$$

#### Straight line fit

A standard task of parameter estimation is fitting a **linear model function** $\lambda_i = a_0 + a_1 x_i$ (linear in the positions $x_i$ and linear in the parameters $a_0$ and $a_1$) to $n$ uncorrelated data points $(x_i,y_i)$ with known variances $\sigma_i^2$. With the matrix notation introduced above:
$$
\mathbf{a} =
\begin{pmatrix}
a_0\\
a_1
\end{pmatrix}, \quad
\mathbf{A} =
\begin{pmatrix}
1 & x_1\\
\vdots & \vdots\\
1 & x_n\\
\end{pmatrix},
$$
so that the product results in a vector of model functions for each position $x_i$:
$$
\boldsymbol{\lambda} = \mathbf{A} \,\mathbf{a} =
\begin{pmatrix}
a_0 + a_1 x_1\\
\vdots \\
a_0 + a_1 x_n\\
\end{pmatrix}.
$$
Since the data points are uncorrelated, their covariance matrix $\mathbf{V}$ is diagonal, with the entries on the diagonal consisting of the variances. This means that the inverse covariance matrix $\mathbf{V}^{-1}$ is also diagonal and consists of the reciprocals of the variances. We refer to these (as with the weighted mean above) as weights, with the abbreviation $w_i\equiv 1/\sigma_i^2$:
$$
\mathbf{V} =
\begin{pmatrix}
\sigma_1^2 & \cdots & 0 \\
\vdots & \ddots & \vdots \\
0 & \cdots & \sigma_n^2
\end{pmatrix} \quad\to\quad
\mathbf{V}^{-1} =
\begin{pmatrix}
\frac{1}{\sigma_1^2} & \cdots & 0 \\
\vdots & \ddots & \vdots \\
0 & \cdots & \frac{1}{\sigma_n^2}
\end{pmatrix} \equiv
\begin{pmatrix}
w_1 & \cdots & 0 \\
\vdots & \ddots & \vdots \\
0 & \cdots & w_n
\end{pmatrix}.
$$

For this choice of $\mathbf{a}$, $\mathbf{A}$ and $\mathbf{V}^{-1}$, the estimated value for the parameters can now be calculated:
$$
\hat{\mathbf{a}} =
(\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^{-1}
\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y}.
$$
Here, too, the result is given first, followed by the auxiliary calculation below:
$$
\hat{\mathbf{a}} =
\begin{pmatrix}
\hat{a}_0\\\
\hat{a}_1
\end{pmatrix} =
\frac{1}{(\sum_i w_i)(\sum_i w_i x_i^2)-(\sum_i w_i x_i)^2}
\begin{pmatrix}
(\sum w_i x_i^2)(\sum w_i y_i) - (\sum_i w_i x_i)(\sum w_i x_i y_i) \\
(\sum_i w_i x_i)(\sum w_i x_i y_i) - (\sum w_i x_i)(\sum w_i y_i)\\
\end{pmatrix}.
$$
We thus obtain a (reasonably compact) equation for the estimated values of the $y$-axis intercept $\hat{a}_0$ and the slope $\hat{a}_1$ of the line. In earlier times, this equation was provided in physics laboratory courses for entering in a pocket calculator, later in a a computer. Today, it is already implemented in a number of software tools. Nevertheless, an understanding of how it comes about is essential for natural scientists.

There is also a compact representation for the covariance matrix of the parameters $\hat{a}_0$ and $\hat{a}_1$:
$$
\mathbf{V}[\hat{\mathbf{a}}] =
(\mathbf{A}^\mathsf{T}\,
\mathbf{V}^{-1}\,
\mathbf{A})^{-1} =
\frac{1}{(\sum_i w_i)(\sum_i w_i x_i^2)-(\sum_i w_i x_i)^2}
\begin{pmatrix}
\sum_i w_i x_i^2 & -\sum_i w_i x_i \\
-\sum_i w_i x_i & \sum_i w_i\\
\end{pmatrix}.
$$
An essential result of this calculation is that $y$-intercept and slope are generally **anticorrelated**, as the non-diagonal elements are negative and thus also the correlation coefficient. This was also to be expected, as a steeper slope leads to a smaller $y$-intercept and vice versa.

This anti-correlation can be avoided by a clever **coordinate transformation**. The idea is to move the measurement points so that the new $y$-axis lies "in the middle" of the measurement points. The center is the weighted mean value discussed above
$$
\overline{x} = \frac{1}{\sum_i w_i} \sum_i w_i x_i.
$$
The coordinate transformation is
$$
x_i \to x_i^\prime = x_i - \overline{x} = x_i - \frac{\sum_i w_i x_i}{\sum_i w_i}.
$$
The non-diagonal element of the covariance matrix thus disappears:
$$
-\sum_i w_i x_i^\prime =
-\sum_i w_i \left( x_i - \frac{\sum_i w_i x_i}{\sum_i w_i} \right) =
-\sum_i w_i x_i + \sum_i w_i\frac{\sum_i w_i x_i}{\sum_i w_i} = 0.
$$
The following example code shows this using a straight line fit to three data points. After a shift by the weighted mean value, the correlation coefficient disappears (except for numerical inaccuracies).


In [ ]:
"""straight-line fit without parameter correlations"""
import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit

n = 3
xdata  = np.array( [ 1.0, 2.0, 3.0 ] )
ydata  = np.array( [ 1.5, 3.6, 4.1 ] )
ey     = np.array( [ 0.5, 0.8, 0.3 ] )

def lin_model( x, a0=1., a1=1. ):
	'''linear model (straight-line fit)'''
	return a0 + a1*x

# plot data points
fig,ax = plt.subplots( 1,2,figsize=([15,5]) )
ax[0].errorbar( xdata, ydata, ey,fmt='bo') 
ax[0].set_xlabel('$x$')
ax[0].set_ylabel('$y$')

# fit with curve_fit (uncertainty only correct when explicitly switching on absolute uncertainites)
popt, pcov = curve_fit( lin_model, xdata, ydata, sigma=ey, absolute_sigma=True )

# plot fitted curve
xrange = np.linspace( 0.5, 3.5, 200 )
ax[0].plot( xrange, lin_model( xrange, *popt), 'r-' )

# print fit parametera
prho = pcov[1][0]/np.sqrt(pcov[0][0]*pcov[1][1])
print( "--- Before parameter transformation --- ")
print( "Parameters:                  ", popt )
print( "Correlation coefficient:     ", prho )
print( "Covariance matrix:\n", pcov )
ax[0].text( 0.5, 4.5, r"before: $\rho$ = %5.3f" % prho )

# parameter transformation
shift = np.average( xdata, weights=1./ey**2)
xdata = xdata - shift

# plot shifted data points
ax[1].errorbar( xdata, ydata, ey,fmt='bo') 
ax[1].set_xlabel( r'$x^\prime$')
ax[1].set_ylabel( r'$y$')

# fit with curve_fit (uncertainty only correct when explicitly switching on absolute uncertainites)
popt, pcov = curve_fit( lin_model, xdata, ydata, sigma=ey, absolute_sigma=True )

# plot fitted curve
xrange = np.linspace( 0.5-shift, 3.5-shift, 200 )
ax[1].plot( xrange, lin_model( xrange, *popt), 'r-' )

# print fit parameters
prho = pcov[1][0]/np.sqrt(pcov[0][0]*pcov[1][1])
print( r"--- After parameter transformation x' = x - %5.3f --- " % shift )
print( "Parameters:                  ", popt )
print( "Correlation coefficient:     ", prho )
print( "Covariance matrix:\n", pcov )
ax[1].text( 0.5-shift, 4.5, r"after: $\rho$ = %5.3e" % prho )

plt.show()

>**Auxiliary calculation 3: stratigh line fit**
>
>In this auxiliary calculation, the variables that are included in the estimated values for the line parameters and their covariance matrix are to be calculated:
>$$
\begin{split}
\mathbf{A}^\mathsf{T}
\mathbf{V}^{-1}
\mathbf{A}
&=
\begin{pmatrix}
1 & \cdots & 1 \\
x_1 & \cdots & x_n
\end{pmatrix}
\begin{pmatrix}
w_1 & \cdots & 0 \\
\vdots & \ddots & \vdots \\
0 & \cdots & w_n
\end{pmatrix}
\begin{pmatrix}
1 & x_1\\
\vdots & \vdots\\
1 & x_n\\
\end{pmatrix} \\
&=
\begin{pmatrix}
w_1 & \cdots & w_n \\
w_1 x_1 & \cdots & w_n x_n \\
\end{pmatrix}
\begin{pmatrix}
1 & x_1\\
\vdots & \vdots\\
1 & x_n\\
\end{pmatrix} \\
&=
\begin{pmatrix}
\sum_i w_i & \sum_i w_i x_i \\
\sum_i w_i x_i & \sum_i w_i x_i^2\\
\end{pmatrix}.
\end{split}
>$$
>The determinant of this $2\times2$-matrix is
>$$
\mathsf{det}(\mathbf{A}^\mathsf{T}
\mathbf{V}^{-1}
\mathbf{A}) =
\left(\sum_i w_i\right)\left(\sum_i w_i x_i^2\right)-\left(\sum_i w_i x_i\right)^2.
>$$
>The matrix can be inverted easily (swapping the diagonal elements, minus sign in front of non-diagonal elements, division by determinant), this is the expression for the covariance matrix of the parameters:
>$$
(\mathbf{A}^\mathsf{T}
\mathbf{V}^{-1}
\mathbf{A})^{-1}
 =\frac{1}{\mathsf{det}(\mathbf{A}^\mathsf{T} \,
\mathbf{V}^{-1}\,
\mathbf{A}) }
\begin{pmatrix}
\sum_i w_i x_i^2 & -\sum_i w_i x_i \\
-\sum_i w_i x_i & \sum_i w_i\\
\end{pmatrix}.
>$$
>For the estimated value of the parameters we still require:
>$$
\mathbf{A}^\mathsf{T}
\mathbf{V}^{-1}
\mathbf{y} =
\begin{pmatrix}
w_1 & \cdots & w_n \\
w_1 x_1 & \cdots & w_n x_n \\
\end{pmatrix}
\begin{pmatrix}
y_1\\
\vdots\\
y_n
\end{pmatrix} =
\begin{pmatrix}
\sum_i w_i y_i \\
\sum_i w_i x_i y_i
\end{pmatrix}
>$$
> and thus finally:
>$$
\begin{split}
\hat{\mathbf{a}} &=
\begin{pmatrix}
\hat{a}_0\\\
\hat{a}_1
\end{pmatrix} =
(\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{A})^{-1}
\mathbf{A}^\mathsf{T} \mathbf{V}^{-1} \mathbf{y} \\
&=\frac{1}{\mathsf{det}(\mathbf{A}^\mathsf{T} \,
\mathbf{V}^{-1}\,
\mathbf{A}) }
\begin{pmatrix}
\sum_i w_i x_i^2 & -\sum_i w_i x_i \\
-\sum_i w_i x_i & \sum_i w_i\\
\end{pmatrix}
\begin{pmatrix}
\sum_i w_i y_i \\
\sum_i w_i x_i y_i
\end{pmatrix} \\
&=\frac{1}{(\sum_i w_i)(\sum_i w_i x_i^2)-(\sum_i w_i x_i)^2}
\begin{pmatrix}
(\sum w_i x_i^2)(\sum w_i y_i) - (\sum_i w_i x_i)(\sum w_i x_i y_i) \\
(\sum_i w_i x_i)(\sum w_i x_i y_i) - (\sum w_i x_i)(\sum w_i y_i)\\
\end{pmatrix}.
\end{split}
>$$

### Goodness of fit
In the least squares method (LS method), a given model function $\boldsymbol{\lambda}$ is compared with data and the parameters of the function are adjusted so that they best fit the data. In the LS method, "best" means that the residual sum of squares,
$$
S \equiv \chi^2 \equiv
(\mathbf{y} - \boldsymbol{\lambda}(\mathbf{x};\mathbf{a}))^\mathsf{T} \,
\mathbf{V}^{-1} \,
(\mathbf{y} - \boldsymbol{\lambda}(\mathbf{x};\mathbf{a})),
$$
is minimized. However, this does not mean that the model function was chosen sensibly and describes the data well. A bad choice of a model function would be, for example, a linear function that is used to fit data that is not compatible with a straight line. A bad fit would also result if the covariance matrix $\mathbf{V}$ of the model parameters assumes uncertainties that are too large or too small or incorrect correlations.

We are looking for a criterion to quantify the **goodness of fit** (GoF). There is such a criterion for the LS method because the probability distribution of $S$ is known: at least for normally distributed measured values, $S$ follows a $\chi^2$ distribution.  If, after minimizing $S$, a value of $S$ is found that is very unlikely based on the $\chi^2$ distribution, this is an indication that either the **model function is unsuitable** or the **uncertainties have been incorrectly estimated**.

For $n$ normally distributed measured values $y_i$ and $m$ model parameters $a_i$, the residual sum of squares follows a $\chi^2$ distribution (see Chapter 2) with $n_\mathsf{dof}=n-m$ degrees of freedom (dof):
$$
\chi^2(S;n_\mathsf{dof}) = \frac{S^{\frac{n_\mathsf{dof}}{2}-1}}
{2^{\frac{n_\mathsf{dof}}{2}}\Gamma(\frac{n_\mathsf{dof}}{2})}
\exp\left[-\frac{S}{2}\right].
$$
If $m$ parameters are to be determined from $n$ data points, then the number of degrees of freedom is given by the difference $n-m$, so $n_\mathsf{dof}$ is a measure of how many excess data points are available compared to the number of parameters to be determined, i.e., how many data points are "still free" on average and not necessary for determining the parameters. As a reminder: the expected value of the $\chi^2$-PDF is $\mathsf{E}[S]=n_\mathsf{dof}$ and the variance $\mathsf{V}[S]=2n_\mathsf{dof}$.

With this known probability distribution, its integrated probability can be used for a goodness-of-fit test. The measure of goodness-of-fit is the **$\chi^2$ probability** $P_{\chi^2}$. This is defined as the probability of finding an **observed value of $S_0$ or greater**:
$$
P_{\chi^2} = \int_{S_0}^\infty \chi^2(S;n_\mathsf{dof}) \,\mathsf{d} S.
$$
This corresponds to the total probability 1 minus the CDF of the $\chi^2$ distribution for the value $S_0$. In SciPy, this value can be calculated via `1.-scipy.stats.chi2.cdf(S0,ndof)`. Even if the full $\chi^2$ CDF is not at hand, the quality of the fit can be approximately checked by normalizing the probability for $S_0$ to the number of degrees of freedom $n_\mathsf{dof}$. As shown in the figure below, the probability for $S_0/n_\mathsf{dof}$ is approximately 40%, approximately independent of $n_\mathsf{dof}$. This value $S_0/n_\mathsf{dof}$ can therefore be used as an **approximate measure of the goodness of fit**: a good fit has $S_0/n_\mathsf{dof}\approx 1$. If $S_0/n_\mathsf{dof}$ is much larger or much smaller than 1, either the model function is unsuitable or the uncertainties have been estimated incorrectly.

In [ ]:
""" display chi2 probability and chi2 probability normalized to number of degrees of freedom"""
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import chi2

fig,ax = plt.subplots( 1, 2, figsize=(10,5) )

S = np.linspace( 0, 25, 250 )
ndof = np.array( [ 2, 4, 6, 8, 10 ] )
for n in ndof:
    ax[0].plot( S, 1.-chi2.cdf( S, n ), label=r'$n_\mathsf{dof}$ = %d' % n  )
    ax[1].plot( S/n, (1.-chi2.cdf( S, n ) ) )

ax[0].set_xlabel( r'$\chi^2$' )
ax[0].set_ylabel( r'$P_{\chi^2}$' )
ax[0].set_ylim( 0., 1.05 )
ax[0].legend()

ax[1].vlines( 1, 0, 1, linestyles="dashed", colors="red" )
ax[1].set_xlabel( r'$\chi^2/n_\mathsf{dof}$' )
ax[1].set_ylabel( r'$P_{\chi^2}$' )
ax[1].set_xlim( 0, 3 )
ax[1].set_ylim( 0., 1.05 )

plt.show()